# Slime Mold Simulation

In [1]:
import numpy as np
import matplotlib.pyplot as plt
from matplotlib import image
import matplotlib as mpl

In [2]:
def lonLatToYX(lon, lat):
    y = H - H * (lon - lon0) / (lon1 - lon0)
    x =  W - W * (lat - lat1) / (lat0 - lat1)
    return x, y

In [3]:
# usamap = image.imread('usamap.png')[:, :, 0]
# H, W = usamap.shape[0], usamap.shape[1]
# for i in range(H):
#     for j in range(W):
#         usamap[i, j] = 1 -usamap[i, j]
# usamap[0,0] = 1
# usamap[0,1] = 0
# # plt.rcParams['figure.figsize'] = (12,12)
# plt.imshow(usamap, cmap = 'gray')
# lat0, lat1 = 125, 65
# lon0, lon1 = 25, 50
# cities = np.loadtxt('cities.txt', dtype=str, delimiter='	', usecols = (1, 10 ,11))
# topPop = 32

# foods = []
# for city in cities[:topPop]:
#     lon, lat = float(city[1]), float(city[2])
#     x, y = lonLatToYX(lon, lat)
#     foods += [(int(y), int(x))]
#     plt.plot(x, y, "ro")
# plt.show()

In [4]:
n = 200
H, W = n, n
trail = np.zeros((H, W))
trail1 = np.zeros((H, W))
deposit = 0.6
sensor_distance = 2
sensor_angle = 15 * np.pi / 180
turn_angle = 15  * np.pi / 180#sensor_angle
decay = 0.9
speed = 2
weights = np.array([1/16, 1/8, 1/16, 
                   1/8, 1/4, 1/8,
                   1/16, 1/8, 1/16])


foods = [(50, 50), (100, 20), (160, 171), (180, 171), (30, 150), (80, 80)]
foodFound = [False for food in foods]

for food in foods:        
    for i in range(-3, 4):
        for j in range(-3, 4):
            trail[food[0] + i, food[1] + j] = 1


In [5]:
baseCnt = 1
bases = [(100, 100)]
foodCnt = 0
baseIdx = 0

In [6]:
class SlimeMoldCell():    
    def __init__(self, x, y, direction):
        self.x = x
        self.y = y
        self.direction = direction
        self.stopped = False
        self.deposit = 0.6
        global speed
        self.speed = speed * 0.75 * (1 + np.random.random())
        self.path = []
        #self.decay #decays slower when touched food        

    def reset(self, dira):
        global baseIdx
        baseIdx = (baseIdx + 1) % baseCnt
        self.x, self.y = bases[baseIdx]
        self.direction = dira[baseIdx]
        self.path = []      

    def reset1(self, idx, dira):
        self.x, self.y = bases[idx]
        self.direction = dira[idx] + (np.random.random() - 0.5)* np.pi /3#np.random.random() * 2 * np.pi 
        self.path = []

    def move(self, dira):
        self.x += self.speed * np.cos(self.direction)
        self.y += self.speed * np.sin(self.direction)
        if self.x < 0 or self.x >= H or self.y < 0 or self.y >= W:
            self.reset(dira)
        else:            
            self.path += [(self.x, self.y)]
        #else 
        #    self.direction += (np.random.random() - 0.5) * (10 * np.pi / 180)
    
    def getDeposit(self):
        return self.deposit
    
    def setDeposit(self, deposit):
        self.deposit = deposit

    def addDeposit(self, deposit):
        self.deposit += deposit
        
    def getX(self):
        return int(self.x)
    
    def getY(self):
        return int(self.y)
    
    def turnClockwise(self, direction):
        self.direction -= direction
        
    def forwardSensor(self):
        x = int(n + self.x + sensor_distance * np.cos(self.direction)) % H
        y = int(n + self.y + sensor_distance * np.sin(self.direction)) % W
        return (x, y)
    
    def rightSensor(self):
        x = int(n + self.x + sensor_distance * np.cos(self.direction - sensor_angle)) % H
        y = int(n + self.y + sensor_distance * np.sin(self.direction - sensor_angle)) % W
        return (x, y)
    
    def leftSensor(self):
        x = int(n + self.x + sensor_distance * np.cos(self.direction + sensor_angle)) % H
        y = int(n + self.y + sensor_distance * np.sin(self.direction + sensor_angle)) % W
        return (x, y)
    
    def getPath(self):
        return self.path

#    def nearFood(self, trail):
#        if self.isNearFood():#trail[int(self.x), int(self.y)] > 1:#if (self.x, self.y) in foods:
#            self.turnClockwise(np.pi)
#        elif trail[int(self.x), int(self.y)] > 0:
#            self.setDeposit(0.6)
#        else:
#            self.setDeposit(self.deposit)# * 0.75)
#         if not near food:
#             then decay

    def isNearFood(self):
        for i in range(len(foodFound)):
            food = foods[i]
            if np.abs(self.x- food[0]) < 4 and np.abs(self.y- food[1]) < 4:
                return i
        return -1

In [7]:
data = np.zeros((H, W))
percent = 0.01

startX, startY = bases[0]
slimeCells = []
direction = np.random.random() * 2 * np.pi #in Radian
for i in range(int(percent * H * W)):
    newSlime = SlimeMoldCell(startX, startY, direction) #+ (np.random.random() - 0.5)* np.pi/4)
    slimeCells += [newSlime]
    data[startX, startY] = 1

In [8]:
yellow = (mpl.colors.ListedColormap(['yellow']))

In [9]:
K = 10000
%matplotlib qt

from matplotlib.animation import FFMpegWriter
metadata = dict(title='My first animation in 3D', artist='Matplotlib',comment='Wakanda is here now.')
writer = FFMpegWriter(fps=8, metadata=metadata,bitrate=200000)
fig = plt.figure(dpi=200, frameon=False)

ax = plt.Axes(fig, [0., 0., 1., 1.])
ax.set_axis_off()
fig.add_axes(ax)

angle = np.random.random() * 2 * np.pi
dira = [angle + (np.random.random() * np.pi /2  + np.pi / 4) * i for i in range(len(foods) + 1)]

# plt.rcParams['figure.figsize'] = [8, 8]
with writer.saving(fig, "slimy1.mp4", dpi=200):
    for _ in range(1):
        for k in range(K):
            newData = np.zeros((H, W))
            #Sense and rotate
            for slimeCell in slimeCells:
                x, y = slimeCell.getX(), slimeCell.getY()
                trailL = trail[slimeCell.leftSensor()]
                trailR = trail[slimeCell.rightSensor()]
                trailF = trail[slimeCell.forwardSensor()]

                foodIdx = slimeCell.isNearFood()
                if foodIdx >= 0 and not foodFound[foodIdx]:
                    #slimeCell.addDeposit(deposit)
                    foodFound[foodIdx] = True
                    path = slimeCell.getPath()
                    foodCnt += 1
                    baseCnt += 1
                    bases += [foods[foodIdx]]
                    for x0, y0 in path:
                        trail[int(x0), int(y0)] = 2

                    baseIdx = baseCnt - 1  
                    dira = [ d - (np.random.random() * np.pi / 2  + np.pi / 4) for d in dira]
                    for i in range(0, int(len(slimeCells)/2)):
                        slimeCells[i].reset1(baseIdx,dira)  
                    for i in range(int(len(slimeCells)/2), int(len(slimeCells))):
                        slimeCells[i].reset(dira) 
                else:
                    # if trailF > 0 or trailR > 0 or trailL > 0:
                    #     #dep = 0.95 * np.max([trailF, trailR, trailL])
                    #     slimeCell.addDeposit(deposit)
                    #     trail[x, y] += deposit
#                     if np.random.random() < 1 - 0.3 ** k:
                    if trailF > trailR and trailF > trailL:
                        #no change
                        0
                    elif trailL > trailR:
                        #Turn left
                        slimeCell.turnClockwise(-turn_angle)
                    elif trailR > trailL:
                        slimeCell.turnClockwise(turn_angle)
                    else:
                        rand = np.random.random()
                        if rand > 0.5:
                            slimeCell.turnClockwise(turn_angle)
                        else:
                            slimeCell.turnClockwise(-turn_angle)

            #Move
            for slimeCell in slimeCells:
                x, y = slimeCell.getX(), slimeCell.getY()
                slimeCell.move(dira)
                newData[x, y] = 1

            data = newData

            #Deposit
            for slimeCell in slimeCells:
                x, y = slimeCell.getX(), slimeCell.getY()
                #if trail[x, y] == 0:
                trail1[x, y] += deposit

            newTrail1 = trail1.copy()
            ##Diffusing every cell
            for x in range(1, H - 1):
                for y in range(1, W - 1):
                    # if trail[x - 1, y - 1] > 0 or trail[x - 1, y] > 0 or trail[x - 1, y + 1] > 0 or \
                    #     trail[x, y - 1] > 0 or trail[x, y] > 0 or trail[x, y + 1] > 0 or \
                    #     trail[x + 1, y - 1] > 0 or trail[x + 1, y] > 0 or trail[x + 1, y + 1] > 0:
                    #     continue
                    diffusedT = trail1[x-1, y-1] * weights[0] + trail1[x, y-1] * weights[1] + \
                               trail1[x+1, y-1] * weights[2] + \
                               trail1[x-1, y] * weights[3] + \
                               trail1[x, y] * weights[4] + \
                               trail1[x+1, y  ] * weights[5] + \
                               trail1[x-1, y+1] * weights[6] + \
                               trail1[x, y+1] * weights[7] + \
                               trail1[x+1, y+1] * weights[8]
                    #if diffusedT * decay > 0.1:
                    #diffusedT = trail[x, y]
                    newTrail1[x, y] = min(1, diffusedT * decay)

            trail1 = newTrail1.copy()
        
            for x in range(0, H):
                for y in range(0, W):
                    if trail1[x, y] > 1:
                        trail1[x, y] = 1
            max1 = max([max(a) for a in trail1])
            ##Diffusing every cell
            newTrail = trail.copy()
            for x in range(1, H - 1):
                for y in range(1, W - 1):
                    if trail[x - 1, y - 1] == 0 and trail[x - 1, y] == 0 and trail[x - 1, y + 1] == 0 and \
                        trail[x, y - 1] == 0 and trail[x, y] == 0 and trail[x, y + 1] == 0 and \
                        trail[x + 1, y - 1] == 0 and trail[x + 1, y] == 0 and trail[x + 1, y + 1] == 0:
                        continue
                    diffusedT = trail[x-1, y-1] * weights[0] + trail[x, y-1] * weights[1] + \
                               trail[x+1, y-1] * weights[2] + \
                               trail[x-1, y] * weights[3] + \
                               trail[x, y] * weights[4] + \
                               trail[x+1, y  ] * weights[5] + \
                               trail[x-1, y+1] * weights[6] + \
                               trail[x, y+1] * weights[7] + \
                               trail[x+1, y+1] * weights[8]
            
                    newTrail[x, y] = min(1, diffusedT * decay)

            max2 = max([max(a) for a in newTrail])

            plt.axis('off')
            if foodCnt == len(foods) or k % 1 == 0:
                plt.cla()
                D = (trail1 * (1/max1) + newTrail * (1/max2) + data)/3
                background = np.zeros((n, n))
                plt.axis('off')
                ax.imshow(background, alpha = 0.95)
#                 ax.imshow(usamap, cmap='gray', alpha = 0.95)
                ax.imshow(D, cmap = yellow, alpha = D)
                plt.draw()
                plt.pause(0.1)
                writer.grab_frame()
            if foodCnt == len(foods):
                break

    plt.show()

In [11]:
plt.cla()
# plt.axis('off')
# plt.imshow(usamap, cmap='gray', alpha = 0.95)
plt.imshow(background, alpha = 0.95)
plt.imshow(newTrail, cmap = yellow, alpha = D)
# plt.draw()
plt.show()
plt.savefig("final_map.png")

In [ ]:
plt.imshow(trail, cmap = yellow, )
plt.show()